In [41]:
##package needed to do the exercise
import pandas as pd #package for reading and using dataset
import numpy as np #package needed for inserting value in dataset
from sklearn.metrics import roc_auc_score #needed for determing AUC score
import time as t
begin = t.perf_counter()

In [42]:
df=pd.read_csv('C:/Users/s151675/Documents/Jaar_master_2/Kwartiel 3,4/Master project/Data aangepast/data_for_prediction/data+prediction_final/data_complete_final.csv', delimiter = ';') #read csv file

In [43]:
df #visualize dataset

Case ID                  Activity       Complete Timestamp  \
0       155011  Medicatieverificatie SEH  2019-01-01 00:35:00.000   
1       155013                Radiologie  2019-01-01 00:37:00.000   
2       155020  Medicatieverificatie SEH  2019-01-01 01:29:00.000   
3       155021  Medicatieverificatie SEH  2019-01-01 01:26:00.000   
4       155027  Medicatieverificatie SEH  2019-01-01 01:54:00.000   
...        ...                       ...                      ...   
50078   243220        Pijnscore herhalen  2020-08-02 21:36:00.000   
50079   243221        Pijnscore herhalen  2020-08-02 21:36:00.000   
50080   243223          Beleidsorder SEH  2020-08-02 23:20:00.000   
50081   243224      Beleidsorder SEH-VPL  2020-08-02 22:48:00.000   
50082   243225      Beleidsorder SEH-VPL  2020-08-02 23:51:00.000   

             Variant  Variant index Specialismecode  Age Gender Triage color  \
0       Variant 2252           2252             CHI   26    Man         Geel   
1       Variant 2253           2253             NEU   73    Man       Oranje   
2          Variant 4              4             CHI   32    Man        Groen   
3       Variant 2254           2254             INT   34    Man       Oranje   
4       Variant 1252           1252             CAR   21  Vrouw         Geel   
...              ...            ...             ...  ...    ...          ...   
50078    Variant 455            455             CHI   60  Vrouw        Groen   
50079  Variant 36877          36877             CHI   27    Man         Geel   
50080   Variant 1587           1587             NEU   77  Vrouw         Geel   
50081  Variant 36878          36878             CAR   63  Vrouw         Geel   
50082  Variant 36879          36879             NEU   61    Man       Oranje   

           Transport  ... Labaanvraag_SEH  Rad_to_ext  Consult_SEH  Opname  \
0          Ambulance  ...               1           0            1       1   
1          Ambulance  ...               0           0            0       1   
2      Eigen vervoer  ...               0           0            0       0   
3          Ambulance  ...               1           0            0       1   
4      Eigen vervoer  ...               1           0            0       0   
...              ...  ...             ...         ...          ...     ...   
50078  Eigen vervoer  ...               0           0            0       0   
50079  Eigen vervoer  ...               1           1            0       0   
50080      Ambulance  ...               1           0            0       0   
50081  Eigen vervoer  ...               1           0            0       0   
50082      Ambulance  ...               0           0            0       1   

       Bigger4              ArrivelDate  ArrivelTime               DepartDate  \
0            0  2019-01-01 00:00:00.000  0,024305556  2019-01-01 00:00:00.000   
1            1  2019-01-01 00:00:00.000  0,025694444  2019-01-01 00:00:00.000   
2            0  2019-01-01 00:00:00.000  0,061805556  2019-01-01 00:00:00.000   
3            0  2019-01-01 00:00:00.000  0,059722222  2019-01-01 00:00:00.000   
4            0  2019-01-01 00:00:00.000  0,079166667  2019-01-01 00:00:00.000   
...        ...                      ...          ...                      ...   
50078        0  2020-08-02 00:00:00.000      0,85625  2020-08-02 00:00:00.000   
50079        0  2020-08-02 00:00:00.000  0,895833333  2020-08-02 00:00:00.000   
50080        0  2020-08-02 00:00:00.000  0,972222222  2020-08-03 00:00:00.000   
50081        0  2020-08-02 00:00:00.000  0,941666667  2020-08-03 00:00:00.000   
50082        0  2020-08-02 00:00:00.000  0,969444444  2020-08-03 00:00:00.000   

        DepartTime  Unnamed: 24  
0      0,139583333  0,115277778  
1      0,227083333  0,201388889  
2      0,086111111  0,024305556  
3      0,202083333  0,142361111  
4      0,225694444  0,146527778  
...            ...          ...  
50078  0,909027778  0,052777778  
50079  0,994444444  0,098611111  
5

In [44]:
##packages needed for using decision tree classifier and splitting dataset
from sklearn.tree import DecisionTreeClassifier # Import Decision Tree Classifier
from sklearn.model_selection import train_test_split # Import train_test_split function
from sklearn import metrics #Import scikit-learn metrics module for accuracy calculation

In [45]:
#Considered one-hot-encoding in our data, see report.
spec_dummies = pd.get_dummies(df.Specialismecode) #OneHotencoder used for column job
transport_dummies = pd.get_dummies(df.Transport) #OneHotencoder used for column marital
spec_names = spec_dummies.columns
transport_names = transport_dummies.columns
##replace values from categorical to nummerical 
df = df.replace('Vrouw', 0)
df = df.replace('Man', 1)
##replace values from categorical to nummerical (with order)
df = df.replace('Blauw',0) 
df = df.replace('Groen', 1)
df = df.replace('Geel', 2)
df = df.replace('Oranje', 3)
df = df.replace('Rood', 4)

df = pd.concat([df.iloc[:,0],spec_dummies,df.iloc[:,6:9], transport_dummies, df.iloc[:,11], df.iloc[:,12:20]], axis=1) #Dataset with new numerical columns(job and marital)
df



Case ID  ANE  AVG  CAR  CHI  CTC  DER  GYN  HEM  ICA  ...  \
0       155011    0    0    0    1    0    0    0    0    0  ...   
1       155013    0    0    0    0    0    0    0    0    0  ...   
2       155020    0    0    0    1    0    0    0    0    0  ...   
3       155021    0    0    0    0    0    0    0    0    0  ...   
4       155027    0    0    1    0    0    0    0    0    0  ...   
...        ...  ...  ...  ...  ...  ...  ...  ...  ...  ...  ...   
50078   243220    0    0    0    1    0    0    0    0    0  ...   
50079   243221    0    0    0    1    0    0    0    0    0  ...   
50080   243223    0    0    0    0    0    0    0    0    0  ...   
50081   243224    0    0    1    0    0    0    0    0    0  ...   
50082   243225    0    0    0    0    0    0    0    0    0  ...   

       Trauma helikopter  History_bin  nr_patients_same_spec  \
0                      0            0                      0   
1                      0            0                      0   
2                      0            0                      1   
3                      0            0                      0   
4                      0            0                      0   
...                  ...          ...                    ...   
50078                  0            1                      4   
50079                  0            1                      6   
50080                  0            0                      1   
50081                  0            0                      1   
50082                  0            0                      0   

       nr_patients_total  Presentation_time  Labaanvraag_SEH  Rad_to_ext  \
0                      0                  0                1           0   
1                      1                  0                0           0   
2                      3                  0                0           0   
3                      2                  0                1           0   
4                      4                  0                1           0   
...                  ...                ...              ...         ...   
50078                 13                  8                0           0   
50079                 16                  8                1           1   
50080                  9                  9                1           0   
50081                 11                  9                1           0   
50082                  8                  9                0           0   

       Consult_SEH  Opname  Bigger4  
0                1       1        0  
1                0       1        1  
2                0       0        0  
3                0       1        0  
4                0       0        0  
...            ...     ...      ...  
50078            0       0        0  
50079            0       0        0  
50080            0       0        0  
50081            0       0        0  
50082            0       1        0  

[50083 rows x 44 columns]

In [46]:
##define input variables(X) and output variable(Y)
feature_cols2 = df.columns
feature_cols = feature_cols2[0:df.shape[1]-5]
feature_cols_check = feature_cols2[1:df.shape[1]-1]
feature_cols_x = feature_cols2[1:df.shape[1]-5] # all columns excluding 'y' and case_ID
feature_cols_y = feature_cols2[df.shape[1]-5:df.shape[1]] 
# feature_cols = ['to_extern', 'INT', 'CHI', 'Age', 'registering_time', 'MDL', 'ORT', 'History_bin', 'CAR', 'Triage color', 'NEU','Lab']#take relevant features to speed up process
X = df[feature_cols] #input variables
X_ana = df[feature_cols_x]
X_ana_big = df[feature_cols_check]
y = df[feature_cols_y]# Target variable
print(X)
print(y)


       Case ID  ANE  AVG  CAR  CHI  CTC  DER  GYN  HEM  ICA  ...  Ambulance  \
0       155011    0    0    0    1    0    0    0    0    0  ...          1   
1       155013    0    0    0    0    0    0    0    0    0  ...          1   
2       155020    0    0    0    1    0    0    0    0    0  ...          0   
3       155021    0    0    0    0    0    0    0    0    0  ...          1   
4       155027    0    0    1    0    0    0    0    0    0  ...          0   
...        ...  ...  ...  ...  ...  ...  ...  ...  ...  ...  ...        ...   
50078   243220    0    0    0    1    0    0    0    0    0  ...          0   
50079   243221    0    0    0    1    0    0    0    0    0  ...          0   
50080   243223    0    0    0    0    0    0    0    0    0  ...          1   
50081   243224    0    0    1    0    0    0    0    0    0  ...          0   
50082   243225    0    0    0    0    0    0    0    0    0  ...          1   

       Ambulance (Inzet heli-MMT)  Ambulance (inzet

In [47]:
# Split dataset into training set and test set
X_train_t, X_test_t, y_train, y_test = train_test_split(X, y, test_size=0.3, random_state=1) # divide dataset into 70% training and 30% test
X_train = X_train_t.iloc[:,1:40]
X_test = X_test_t.iloc[:,1:40]
print(X_train)
y_train_lab = y_train.iloc[:,0]
y_train_rad_to_ext = y_train.iloc[:,1]
y_train_consult = y_train.iloc[:,2]
y_train_opname = y_train.iloc[:,3]
y_test_lab = y_test.iloc[:,0]
y_test_rad_to_ext = y_test.iloc[:,1]
y_test_consult = y_test.iloc[:,2]
y_test_opname = y_test.iloc[:,3]
X_number = X_test_t.iloc[:,0] #take caseID from test set to compare with actual value in later phase
###dataset needed for making predictions with already predicted values
X_train_big = pd.concat([X_train_t.iloc[:,1:40],y_train.iloc[:,0:4]], axis=1)
##choose between these test_data set, where perf is with actual values and other is with predicted values
X_test_big = X_test #make this out of prediction
# X_test_big_perf = pd.concat([X_test_t.iloc[:,1:40],y_test.iloc[:,0:4]], axis=1) #to compare with existing values of columns
y_train_big = y_train.iloc[:,-1]
y_test_big = y_test.iloc[:,-1]

       ANE  AVG  CAR  CHI  CTC  DER  GYN  HEM  ICA  INT  ...  Ambulance  \
13254    0    0    1    0    0    0    0    0    0    0  ...          0   
22098    0    0    0    1    0    0    0    0    0    0  ...          0   
29082    0    0    0    0    0    0    0    0    0    1  ...          1   
27661    0    0    0    1    0    0    0    0    0    0  ...          0   
37323    0    0    0    0    0    0    0    0    0    0  ...          1   
...    ...  ...  ...  ...  ...  ...  ...  ...  ...  ...  ...        ...   
50057    0    0    0    1    0    0    0    0    0    0  ...          0   
32511    0    0    0    0    0    0    0    0    0    0  ...          0   
5192     0    0    0    1    0    0    0    0    0    0  ...          0   
12172    0    0    0    0    0    0    0    0    0    0  ...          1   
33003    0    0    0    0    0    0    0    0    0    0  ...          0   

       Ambulance (Inzet heli-MMT)  Ambulance (inzet grond-MMT)  Anders  \
13254                    

In [48]:
#Function made to measure the confusing matrix
def perf_measure(y_actual, y_hat):
    ## start with zero values
    TP = 0
    FP = 0
    TN = 0
    FN = 0
    count = 0 
    for i in range(len(y_hat)): #for all values in the column y_test
        count += 1 #count the total number of rows
        if y_actual[i]==1 and y_hat[i]==1:#True positive
            TP += 1
        if y_hat[i]==1 and y_actual[i]==0:#False positive
            FP += 1
        if y_actual[i]==0 and y_hat[i]==0:#True negative
            TN += 1
        if y_hat[i]==0 and y_actual[i]==1:#False negative
            FN += 1

    return(TP/count, FP/count, TN/count, FN/count, count)#return all relevant values in fractions

In [49]:
def RandomForest(Number_leaves, X_train, y_train, X_test):
    clf = RandomForestClassifier(n_estimators = 100, min_samples_leaf=Number_leaves,class_weight = "balanced") #define decision tree with selected variable
    clf = clf.fit(X_train,y_train) #train the decision tree on training set
    y_pred = clf.predict(X_test) #predict the values of X_test
    
    return(clf, y_pred)


In [50]:
from sklearn.model_selection import KFold, cross_val_score
from sklearn.ensemble import RandomForestClassifier
from sklearn.ensemble import ExtraTreesClassifier
from sklearn.metrics import classification_report, confusion_matrix, accuracy_score

In [51]:
def predict_value(y_train, y_test, X_train, X_test, X_ana, feature_cols2, negative):
    ##used for determing best values
    max_score = 0
    max_AUC = 0
    best_leaves = 0
    y_test = np.array(y_test)
    clf_final, y_pred = RandomForest(2, X_train, y_train, X_test)
    ##loop over values from 2 to 100 for selecting best parameter
    for i in range(2,200):
        clf, y_pred = RandomForest(i,X_train, y_train, X_test)
    #     AUC_score = roc_auc_score(y_test,y_pred)
    #     print(accuracy_score(y_test_lab, y_pred))
        TPRate,FPRate,TNRate, FNRate, count = perf_measure(y_test, y_pred) #call confusing matrix function to determine these values in matrix
        if(negative==False):
            accuracy = (TPRate+TNRate)/(TPRate+TNRate+FPRate+FNRate)
            print("accuracy :", accuracy," for num of leaves =", i)
        else:
            accuracy = TNRate/(TNRate+FNRate)
            print("Negative prediction value :", accuracy," for num of leaves =", i)
        ##function used for updating best score if one score exceed previously best scores
        
        if accuracy>=max_score:
            max_score = accuracy
            best_leaves = i
            clf_final = clf
    
    clf, y_pred = RandomForest(best_leaves,X_train, y_train, X_test) #Best decision tree based on highest accuracy 
    TPRate,FPRate,TNRate, FNRate, count = perf_measure(y_test, y_pred) #call confusing matrix function to determine these values in matrix
    p = (((TNRate+FPRate)*count)/count*((TNRate+FNRate)*count)/count) #measure p value for best model based on recall & AUC score
    kappa_score = (metrics.accuracy_score(y_test, y_pred)-p)/(1-p) #measure Kappa score for best model based on recall & AUC score
    AUC_score = roc_auc_score(y_test,y_pred) #measure AUC score for best model based on recall & AUC score
    ##measure Accuracy score for best model based on Recall & AUC score
    accuracy = (TPRate+TNRate)/(TPRate+TNRate+FPRate+FNRate)

    ###feature importance start
    forest = ExtraTreesClassifier(n_estimators=100,min_samples_leaf=best_leaves, class_weight = "balanced")
    forest = forest.fit(X_train,y_train)

    importances = forest.feature_importances_
    std = np.std([tree.feature_importances_ for tree in forest.estimators_],
             axis=0)
    indices = np.argsort(importances)[::-1]
    ##print all scores for best model based on recall & AUC score
    print("best number of leaves = ", best_leaves, " with score = ", max_score, " and accuracy = ", accuracy)
    print("kappa score =", kappa_score)
    print("AUC score =", AUC_score)
    print(confusion_matrix(y_test,y_pred))
    # Print the feature ranking
    print("Feature ranking:")
    for f in range(X_ana.shape[1]):
        print("%d. %s (%f)" % (f + 1, feature_cols2[indices[f]], importances[indices[f]]))
    return(clf_final)


In [52]:
forest_lab = predict_value(y_train_lab, y_test_lab, X_train, X_test, X_ana, feature_cols_x, False)
forest_rad_to_ext = predict_value(y_train_rad_to_ext, y_test_rad_to_ext, X_train, X_test, X_ana, feature_cols_x, False)
forest_consult = predict_value(y_train_consult, y_test_consult, X_train, X_test, X_ana, feature_cols_x, False)
forest_opname = predict_value(y_train_opname, y_test_opname, X_train, X_test, X_ana, feature_cols_x, False)

lab_prediction = forest_lab.predict(X_test)
rad_to_ext_prediction = forest_rad_to_ext.predict(X_test)
consult_prediction = forest_consult.predict(X_test)
opname_prediction = forest_opname.predict(X_test)
X_test_big.insert(38,"labaanvraag", lab_prediction)
X_test_big.insert(39,"rad_to_ext", rad_to_ext_prediction)
X_test_big.insert(40,"consult", consult_prediction)
X_test_big.insert(41,"opname", opname_prediction)
forest_big4 = predict_value(y_train_big, y_test_big, X_train_big, X_test_big, X_ana_big, feature_cols_check, True) ##have to change X_train last features
big4_prediction = forest_big4.predict(X_test_big)
X_test_big.insert(42,"bigger than 4", big4_prediction)
eind = t.perf_counter()
print("number of seconds =", eind-begin)
dataframeafter = pd.concat([X_number,X_test_big.iloc[:,0:43]],axis=1) ##add bigger4 prediction
dataframeafter.to_csv('C:/Users/s151675/Documents/Jaar_master_2/Kwartiel 3,4/Master project/Data aangepast/Data_for_prediction/final_testgroup_prediction.csv')

accuracy : 0.8081863560732113  for num of leaves = 2
accuracy : 0.8049251247920134  for num of leaves = 3
accuracy : 0.7988685524126456  for num of leaves = 4
accuracy : 0.7956738768718802  for num of leaves = 5
accuracy : 0.7929450915141432  for num of leaves = 6
accuracy : 0.7924126455906823  for num of leaves = 7
accuracy : 0.7912146422628952  for num of leaves = 8
accuracy : 0.7898169717138104  for num of leaves = 9
accuracy : 0.7880199667221298  for num of leaves = 10
accuracy : 0.7854242928452579  for num of leaves = 11
accuracy : 0.7836938435940101  for num of leaves = 12
accuracy : 0.7844925124792014  for num of leaves = 13
accuracy : 0.7858901830282862  for num of leaves = 14
accuracy : 0.7836272878535774  for num of leaves = 15
accuracy : 0.784891846921797  for num of leaves = 16
accuracy : 0.7798336106489184  for num of leaves = 17
accuracy : 0.7822296173044925  for num of leaves = 18
accuracy : 0.7767720465890183  for num of leaves = 19
accuracy : 0.7814975041597337  for nu

accuracy : 0.7635940099833611  for num of leaves = 154
accuracy : 0.7645923460898503  for num of leaves = 155
accuracy : 0.762928452579035  for num of leaves = 156
accuracy : 0.7607986688851913  for num of leaves = 157
accuracy : 0.7595341098169718  for num of leaves = 158
accuracy : 0.7581364392678869  for num of leaves = 159
accuracy : 0.765324459234609  for num of leaves = 160
accuracy : 0.7658569051580699  for num of leaves = 161
accuracy : 0.7652579034941764  for num of leaves = 162
accuracy : 0.7639267886855241  for num of leaves = 163
accuracy : 0.7588685524126456  for num of leaves = 164
accuracy : 0.7702495840266224  for num of leaves = 165
accuracy : 0.7654575707154743  for num of leaves = 166
accuracy : 0.7683194675540765  for num of leaves = 167
accuracy : 0.7603327787021631  for num of leaves = 168
accuracy : 0.7605990016638935  for num of leaves = 169
accuracy : 0.7594009983361065  for num of leaves = 170
accuracy : 0.7667886855241265  for num of leaves = 171
accuracy : 0

accuracy : 0.6636272878535774  for num of leaves = 88
accuracy : 0.6603660565723793  for num of leaves = 89
accuracy : 0.6642262895174709  for num of leaves = 90
accuracy : 0.6607653910149751  for num of leaves = 91
accuracy : 0.6624292845257904  for num of leaves = 92
accuracy : 0.6666222961730449  for num of leaves = 93
accuracy : 0.6569717138103162  for num of leaves = 94
accuracy : 0.6626955074875208  for num of leaves = 95
accuracy : 0.6634276206322796  for num of leaves = 96
accuracy : 0.6622961730449252  for num of leaves = 97
accuracy : 0.6644925124792014  for num of leaves = 98
accuracy : 0.6622296173044925  for num of leaves = 99
accuracy : 0.6613643926788686  for num of leaves = 100
accuracy : 0.6633610648918469  for num of leaves = 101
accuracy : 0.6629617304492512  for num of leaves = 102
accuracy : 0.660432612312812  for num of leaves = 103
accuracy : 0.6624292845257904  for num of leaves = 104
accuracy : 0.6639600665557405  for num of leaves = 105
accuracy : 0.6594342762

accuracy : 0.6702163061564059  for num of leaves = 21
accuracy : 0.6622961730449252  for num of leaves = 22
accuracy : 0.6637603993344426  for num of leaves = 23
accuracy : 0.665424292845258  for num of leaves = 24
accuracy : 0.6636272878535774  for num of leaves = 25
accuracy : 0.6583693843594011  for num of leaves = 26
accuracy : 0.6673544093178037  for num of leaves = 27
accuracy : 0.6581031613976706  for num of leaves = 28
accuracy : 0.6579034941763727  for num of leaves = 29
accuracy : 0.6550415973377703  for num of leaves = 30
accuracy : 0.6533777038269551  for num of leaves = 31
accuracy : 0.6528452579034942  for num of leaves = 32
accuracy : 0.652712146422629  for num of leaves = 33
accuracy : 0.6548419301164726  for num of leaves = 34
accuracy : 0.6518469217970051  for num of leaves = 35
accuracy : 0.6509151414309484  for num of leaves = 36
accuracy : 0.648252911813644  for num of leaves = 37
accuracy : 0.6467886855241265  for num of leaves = 38
accuracy : 0.6488519134775375  

accuracy : 0.6211647254575707  for num of leaves = 172
accuracy : 0.6255574043261232  for num of leaves = 173
accuracy : 0.6202329450915142  for num of leaves = 174
accuracy : 0.6268885191347754  for num of leaves = 175
accuracy : 0.622495840266223  for num of leaves = 176
accuracy : 0.6267554076539101  for num of leaves = 177
accuracy : 0.6256905158069884  for num of leaves = 178
accuracy : 0.6198336106489185  for num of leaves = 179
accuracy : 0.6220299500831947  for num of leaves = 180
accuracy : 0.6197670549084858  for num of leaves = 181
accuracy : 0.6210981697171382  for num of leaves = 182
accuracy : 0.6274875207986689  for num of leaves = 183
accuracy : 0.6185024958402663  for num of leaves = 184
accuracy : 0.6187687188019967  for num of leaves = 185
accuracy : 0.6238269550748752  for num of leaves = 186
accuracy : 0.6239600665557404  for num of leaves = 187
accuracy : 0.6232945091514144  for num of leaves = 188
accuracy : 0.6238269550748753  for num of leaves = 189
accuracy : 

accuracy : 0.6793344425956739  for num of leaves = 106
accuracy : 0.6841930116472545  for num of leaves = 107
accuracy : 0.6813311148086523  for num of leaves = 108
accuracy : 0.6803993344425957  for num of leaves = 109
accuracy : 0.6831946755407654  for num of leaves = 110
accuracy : 0.6805990016638935  for num of leaves = 111
accuracy : 0.6819966722129784  for num of leaves = 112
accuracy : 0.6803993344425957  for num of leaves = 113
accuracy : 0.6819301164725458  for num of leaves = 114
accuracy : 0.6835940099833611  for num of leaves = 115
accuracy : 0.6817304492512479  for num of leaves = 116
accuracy : 0.6806655574043261  for num of leaves = 117
accuracy : 0.6793344425956739  for num of leaves = 118
accuracy : 0.6834608985024958  for num of leaves = 119
accuracy : 0.6829284525790349  for num of leaves = 120
accuracy : 0.6798668885191348  for num of leaves = 121
accuracy : 0.6845257903494176  for num of leaves = 122
accuracy : 0.6812645590682197  for num of leaves = 123
accuracy :

Negative prediction value : 0.7912846767472318  for num of leaves = 30
Negative prediction value : 0.7886033785391386  for num of leaves = 31
Negative prediction value : 0.7897325176922155  for num of leaves = 32
Negative prediction value : 0.7900059488399762  for num of leaves = 33
Negative prediction value : 0.7917977256230341  for num of leaves = 34
Negative prediction value : 0.7898419592230667  for num of leaves = 35
Negative prediction value : 0.7896319461149867  for num of leaves = 36
Negative prediction value : 0.7904270633397313  for num of leaves = 37
Negative prediction value : 0.79015606242497  for num of leaves = 38
Negative prediction value : 0.7926356589147286  for num of leaves = 39
Negative prediction value : 0.7895865602287621  for num of leaves = 40
Negative prediction value : 0.7896000960730155  for num of leaves = 41
Negative prediction value : 0.7918677606177607  for num of leaves = 42
Negative prediction value : 0.7902232951116476  for num of leaves = 43
Negative

Negative prediction value : 0.7877108433734941  for num of leaves = 145
Negative prediction value : 0.7885735080058225  for num of leaves = 146
Negative prediction value : 0.7883398247322297  for num of leaves = 147
Negative prediction value : 0.7898612986375353  for num of leaves = 148
Negative prediction value : 0.7871124620060791  for num of leaves = 149
Negative prediction value : 0.7868357487922706  for num of leaves = 150
Negative prediction value : 0.7894090183069172  for num of leaves = 151
Negative prediction value : 0.7911236783870176  for num of leaves = 152
Negative prediction value : 0.7882238914465713  for num of leaves = 153
Negative prediction value : 0.7876382876382877  for num of leaves = 154
Negative prediction value : 0.7881902940473345  for num of leaves = 155
Negative prediction value : 0.7894544123031856  for num of leaves = 156
Negative prediction value : 0.786299060919817  for num of leaves = 157
Negative prediction value : 0.7893967093235832  for num of leaves

In [53]:
print(X_train_big)
print(X_test_big)

       ANE  AVG  CAR  CHI  CTC  DER  GYN  HEM  ICA  INT  ...  Eigen vervoer  \
13254    0    0    1    0    0    0    0    0    0    0  ...              1   
22098    0    0    0    1    0    0    0    0    0    0  ...              1   
29082    0    0    0    0    0    0    0    0    0    1  ...              0   
27661    0    0    0    1    0    0    0    0    0    0  ...              1   
37323    0    0    0    0    0    0    0    0    0    0  ...              0   
...    ...  ...  ...  ...  ...  ...  ...  ...  ...  ...  ...            ...   
50057    0    0    0    1    0    0    0    0    0    0  ...              1   
32511    0    0    0    0    0    0    0    0    0    0  ...              1   
5192     0    0    0    1    0    0    0    0    0    0  ...              1   
12172    0    0    0    0    0    0    0    0    0    0  ...              0   
33003    0    0    0    0    0    0    0    0    0    0  ...              1   

       Trauma helikopter  History_bin  nr_patients_

In [54]:
import pickle
# save the model to disk
filename1 = 'lab.sav'
pickle.dump(forest_lab, open(filename1, 'wb'))
filename2 ='rad_to_ext.sav'
pickle.dump(forest_rad_to_ext, open(filename2, 'wb'))
filename3= 'consult.sav'
pickle.dump(forest_consult, open(filename3, 'wb'))
filename4 = 'opname.sav'
pickle.dump(forest_opname, open(filename4, 'wb'))
filename5 = 'bigger4.sav'
pickle.dump(forest_big4, open(filename5, 'wb'))

In [55]:
##packages needed for visualize decision tree
from sklearn.tree import export_graphviz
from six import StringIO  
from IPython.display import Image  
import pydotplus

##visualize decision tree
dot_data = StringIO()
export_graphviz(forest_big4.estimators_[5], out_file=dot_data,  
                filled=True, rounded=True,
                special_characters=True,feature_names = feature_cols_check,class_names=['0','1'])
graph = pydotplus.graph_from_dot_data(dot_data.getvalue())  
graph.write_png('decision_tree.png')
Image(graph.create_png())

In [56]:
##predict new patient
df_newp = pd.read_csv('C:/Users/s151675/Documents/Jaar_master_2/Kwartiel 3,4/Master project/Data aangepast/data_for_prediction/data+prediction_final/data_newpatient.csv', delimiter = ';') #read csv file

In [57]:
df_newp

Case ID              Activity       Complete Timestamp        Variant  \
0   242329      Beleidsorder SEH  2020-07-28 12:02:00.000  Variant 36531   
1   242907  Beleidsorder SEH-VPL  2020-07-31 20:26:00.000  Variant 36772   
2   241811    Pijnscore herhalen  2020-07-24 11:58:00.000      Variant 2   

   Variant index Specialismecode  Age Gender Triage color      Transport  \
0          36531             CHI   76    Man         Geel      Ambulance   
1          36772             MDL   52  Vrouw         Geel      Ambulance   
2              2             CHI   50  Vrouw        Groen  Eigen vervoer   

  Dismissal_To  History_bin  nr_patients_same_spec  nr_patients_total  \
0            /            0                      3                 13   
1            /            1                      4                 35   
2            /            0                      5                 17   

   Presentation_time  
0                  4  
1                  7  
2                  4

In [58]:
#preprocessing steps
df_names = df_newp.iloc[:,0]
count = 0
print(len(df_newp))
df_spec = pd.DataFrame({'A' : [1,1,1]})
df_trans = pd.DataFrame({'A' : [1,1,1]})
for i in spec_names:
    spec_one = []
    for number in range(0,len(df_newp)):
        if(df_newp.iloc[number,5]==i):
            spec_one.append(1)
        else:
            spec_one.append(0)
    df_spec.insert(count,i,spec_one)
    count +=1
count = 0
for i in transport_names:
    spec_one = []
    for number in range(0,len(df_newp)):
        if(df_newp.iloc[number,9]==i):
            spec_one.append(1)
        else:
            spec_one.append(0)
    df_trans.insert(count,i,spec_one)
    count +=1

print(df_spec.iloc[:,0:25])
print(df_trans.iloc[:,0:6])
##replace values from categorical to nummerical 
df_newp = df_newp.replace('Vrouw', 0)
df_newp = df_newp.replace('Man', 1)
##replace values from categorical to nummerical (with order)
df_newp = df_newp.replace('Blauw',0) 
df_newp = df_newp.replace('Groen', 1)
df_newp = df_newp.replace('Geel', 2)
df_newp = df_newp.replace('Oranje', 3)
df_newp = df_newp.replace('Rood', 4)

df_newp = pd.concat([df_spec.iloc[:,0:25],df_newp.iloc[:,6:9], df_trans.iloc[:,0:6], df_newp.iloc[:,11:20]], axis=1) #Dataset with new numerical columns(job and marital)
df_newp




3
   ANE  AVG  CAR  CHI  CTC  DER  GYN  HEM  ICA  INT  ...  MDL  NCH  NEU  OOG  \
0    0    0    0    1    0    0    0    0    0    0  ...    0    0    0    0   
1    0    0    0    0    0    0    0    0    0    0  ...    1    0    0    0   
2    0    0    0    1    0    0    0    0    0    0  ...    0    0    0    0   

   ORT  PLA  REU  SEH  URO  VAT  
0    0    0    0    0    0    0  
1    0    0    0    0    0    0  
2    0    0    0    0    0    0  

[3 rows x 25 columns]
   Ambulance  Ambulance (Inzet heli-MMT)  Ambulance (inzet grond-MMT)  Anders  \
0          1                           0                            0       0   
1          1                           0                            0       0   
2          0                           0                            0       0   

   Eigen vervoer  Trauma helikopter  
0              0                  0  
1              0                  0  
2              1                  0  


ANE  AVG  CAR  CHI  CTC  DER  GYN  HEM  ICA  INT  ...  Ambulance  \
0    0    0    0    1    0    0    0    0    0    0  ...          1   
1    0    0    0    0    0    0    0    0    0    0  ...          1   
2    0    0    0    1    0    0    0    0    0    0  ...          0   

   Ambulance (Inzet heli-MMT)  Ambulance (inzet grond-MMT)  Anders  \
0                           0                            0       0   
1                           0                            0       0   
2                           0                            0       0   

   Eigen vervoer  Trauma helikopter  History_bin  nr_patients_same_spec  \
0              0                  0            0                      3   
1              0                  0            1                      4   
2              1                  0            0                      5   

   nr_patients_total  Presentation_time  
0                 13                  4  
1                 35                  7  
2                 17                  4  

[3 rows x 38 columns]

In [59]:
lab_prediction = forest_lab.predict(df_newp)
print(lab_prediction)
rad_to_ext_prediction = forest_rad_to_ext.predict(df_newp)
print(rad_to_ext_prediction)
consult_prediction = forest_consult.predict(df_newp)
print(consult_prediction)
opname_prediction = forest_opname.predict(df_newp)
print(opname_prediction)
df_newp.insert(38,"labaanvraag", lab_prediction)
df_newp.insert(39,"rad_to_ext", rad_to_ext_prediction)
df_newp.insert(40,"consult", consult_prediction)
df_newp.insert(41,"opname", opname_prediction)
big4_prediction = forest_big4.predict(df_newp)
df_newp.insert(42,"big4", big4_prediction)
print(big4_prediction)
print(df_newp)
col_names = df_newp.columns
for i in range(0,len(df_newp)):
    if(df_newp.iloc[i,42]==1):
        print("Watch patient with registration_ID :", df_names.iloc[i])
        print("Focus on activity :")
        for a in range(0,4):
            if(df_newp.iloc[i,38+a]==1):
                print(col_names[38+a])
        print("")

[1 1 0]
[1 0 0]
[0 0 0]
[1 0 0]
[1 1 0]
   ANE  AVG  CAR  CHI  CTC  DER  GYN  HEM  ICA  INT  ...  Trauma helikopter  \
0    0    0    0    1    0    0    0    0    0    0  ...                  0   
1    0    0    0    0    0    0    0    0    0    0  ...                  0   
2    0    0    0    1    0    0    0    0    0    0  ...                  0   

   History_bin  nr_patients_same_spec  nr_patients_total  Presentation_time  \
0            0                      3                 13                  4   
1            1                      4                 35                  7   
2            0                      5                 17                  4   

   labaanvraag  rad_to_ext  consult  opname  big4  
0            1           1        0       1     1  
1            1           0        0       0     1  
2            0           0        0       0     0  

[3 rows x 43 columns]
Watch patient with registration_ID : 242329
Focus on activity :
labaanvraag
rad_to_ext
opname

